In [1]:
import os
import tensorflow as tf

use_cpu = False

if use_cpu:
    os.environ['CUDA_VISIBLE_DEVICES'] = '-1'
    os.environ['CPU_ONLY'] = "TRUE"

    physical_devices = tf.config.list_physical_devices('CPU')

    tf.config.set_logical_device_configuration(
        physical_devices[0],
        [tf.config.LogicalDeviceConfiguration() for i in range(8)])
    logical_devices = tf.config.list_logical_devices('CPU')

    print(logical_devices)
else:
    os.environ['CPU_ONLY'] = "FALSE"
    physical_devices = tf.config.list_physical_devices('GPU')
    print(physical_devices)

[PhysicalDevice(name='/physical_device:GPU:0', device_type='GPU')]


In [2]:
from latentneural.data import DataManager
from latentneural.lfads import LFADS
from latentneural.lfads.train import train
from latentneural.utils import AdaptiveWeights


data_dir = os.path.join('..', '..', 'latentneural', 'data', 'storage', 'lorenz', '20210610T215300')
dataset, settings = DataManager.load_dataset(
    directory=data_dir,
    filename='dataset.h5')

In [3]:
neural_data = dataset['train_data'].astype('float')
valid_neural_data = dataset['valid_data'].astype('float')

In [4]:
from datetime import datetime
logdir = os.path.join(data_dir, 'results_new_lfads', datetime.now().strftime("%Y%m%d-%H%M%S"))

initializer=tf.keras.initializers.VarianceScaling(
    scale=1.0, mode='fan_in', distribution='normal'
)

optimizer = tf.keras.optimizers.Adam(
    learning_rate=1e-2,
    beta_1=0.9, 
    beta_2=0.999,
    epsilon=1e-01)

layer_settings=dict(
    kernel_initializer=initializer,
    kernel_regularizer=tf.keras.regularizers.l2(l=0.1)
)

model = train(
    adaptive_lr=dict(factor=0.95, patience=10, min_lr=1e-5),
    model_settings=dict(
        factors_space=3,
        encoded_space=64,
        max_grad_norm=200,
        encoded_var_max=0.1,
        encoded_var_min=0.1,
        original_generator=False,
        timestep=settings['step'],
        encoder_dense=dict(
            layer_settings),
        dense=layer_settings,
        dense_mean=layer_settings,
        dense_logvar=layer_settings,
        neural_dense=layer_settings,
        encoder=dict(
            layer_settings,
            dropout=0.05),
        decoder=dict(
            kernel_initializer=initializer,
            kernel_regularizer=tf.keras.regularizers.l2(l=1),
            recurrent_regularizer=tf.keras.regularizers.l2(l=1)
        ),
    ), 
    optimizer=optimizer, 
    epochs=2000, 
    logdir=logdir,
    train_dataset=neural_data, 
    val_dataset=valid_neural_data,
    adaptive_weights=AdaptiveWeights(
        initial=[1.0, 0.0, 0.0],
        update_start=[0, 1000, 0],
        update_rate=[0., 0.0005, 0.0005],
        min_weight=[1.0, 0.0, 0.0]
    ),
    batch_size=16
)

/home/alessandrofacchin/miniconda/envs/latentneural/lib/python3.8/site-packages/tensorflow/python/data/ops/dataset_ops.py:3703: UserWarning: Even though the `tf.config.experimental_run_functions_eagerly` option is set, this option does not apply to tf.data functions. To force eager execution of tf.data functions, please use `tf.data.experimental.enable.debug_mode()`.
  warnings.warn(


Epoch 1/2000
5/5 [==============================] - 3s 499ms/step - loss: 1740.9895 - loss/loglike: 1786.6950 - loss/kldiv: 48.1871 - loss/reg: 1083.8631 - weights/loglike: 1.0000 - weights/kldiv: 0.0000e+00 - weights/reg: 5.8333e-04 - learning_rate: 0.0100 - grads/EncoderLSTMForward_lstmcell2: 22.3599 - grads/EncoderLSTMBackward_lstmcell1: 20.2834 - grads/EncoderDense: 3391.2107 - grads/DenseMean: 17.1975 - grads/DecoderGRU_grucell: 458.9074 - grads/Dense: 169.5066 - grads/NeuralDense: 92.6199 - norms/EncoderLSTMForward_lstmcell2: 1972.9826 - norms/EncoderLSTMBackward_lstmcell1: 1981.5853 - norms/EncoderDense: 5950.6540 - norms/DenseMean: 414.3451 - norms/DecoderGRU_grucell: 1976.0526 - norms/Dense: 20.5923 - norms/NeuralDense: 43.0481 - val_loss: 1520.4030 - val_loss/loglike: 1520.4030 - val_loss/kldiv: 48.8014
Epoch 2/2000
5/5 [==============================] - 1s 217ms/step - loss: 1374.2538 - loss/loglike: 1392.8686 - loss/kldiv: 49.3054 - loss/reg: 1084.8998 - weights/loglike: 1.

5/5 [==============================] - 1s 170ms/step - loss: 768.9125 - loss/loglike: 773.7714 - loss/kldiv: 58.9426 - loss/reg: 1084.1276 - weights/loglike: 1.0000 - weights/kldiv: 0.0000e+00 - weights/reg: 0.0231 - learning_rate: 0.0100 - grads/EncoderLSTMForward_lstmcell2: 871.3600 - grads/EncoderLSTMBackward_lstmcell1: 834.0505 - grads/EncoderDense: 100347.0618 - grads/DenseMean: 1063.9860 - grads/DecoderGRU_grucell: 25243.6758 - grads/Dense: 9561.9162 - grads/NeuralDense: 13759.6768 - norms/EncoderLSTMForward_lstmcell2: 38721.6328 - norms/EncoderLSTMBackward_lstmcell1: 38887.9714 - norms/EncoderDense: 117013.8815 - norms/DenseMean: 8134.6021 - norms/DecoderGRU_grucell: 38783.1846 - norms/Dense: 411.9440 - norms/NeuralDense: 863.3328 - val_loss: 780.1851 - val_loss/loglike: 780.1851 - val_loss/kldiv: 62.0590
Epoch 11/2000
5/5 [==============================] - 1s 217ms/step - loss: 758.0622 - loss/loglike: 764.4386 - loss/kldiv: 64.7995 - loss/reg: 1084.1068 - weights/loglike: 1.00

5/5 [==============================] - 1s 265ms/step - loss: 748.4901 - loss/loglike: 748.7811 - loss/kldiv: 83.1791 - loss/reg: 1072.4242 - weights/loglike: 1.0000 - weights/kldiv: 0.0000e+00 - weights/reg: 0.0456 - learning_rate: 0.0100 - grads/EncoderLSTMForward_lstmcell2: 2378.9485 - grads/EncoderLSTMBackward_lstmcell1: 2233.2996 - grads/EncoderDense: 212585.4336 - grads/DenseMean: 3936.9125 - grads/DecoderGRU_grucell: 50642.3991 - grads/Dense: 21855.2363 - grads/NeuralDense: 23512.1628 - norms/EncoderLSTMForward_lstmcell2: 75487.9701 - norms/EncoderLSTMBackward_lstmcell1: 75807.6562 - norms/EncoderDense: 230428.7708 - norms/DenseMean: 15929.5034 - norms/DecoderGRU_grucell: 75493.8132 - norms/Dense: 758.3146 - norms/NeuralDense: 1707.3661 - val_loss: 768.7756 - val_loss/loglike: 768.7756 - val_loss/kldiv: 71.6346
Epoch 20/2000
5/5 [==============================] - 1s 221ms/step - loss: 748.4188 - loss/loglike: 750.4871 - loss/kldiv: 80.5514 - loss/reg: 1069.8894 - weights/loglike:

5/5 [==============================] - 1s 224ms/step - loss: 747.8781 - loss/loglike: 743.1013 - loss/kldiv: 96.6934 - loss/reg: 1035.3231 - weights/loglike: 1.0000 - weights/kldiv: 0.0000e+00 - weights/reg: 0.0681 - learning_rate: 0.0100 - grads/EncoderLSTMForward_lstmcell2: 3868.1745 - grads/EncoderLSTMBackward_lstmcell1: 3604.7254 - grads/EncoderDense: 289157.1745 - grads/DenseMean: 5985.5021 - grads/DecoderGRU_grucell: 71550.2435 - grads/Dense: 33225.1139 - grads/NeuralDense: 32821.9290 - norms/EncoderLSTMForward_lstmcell2: 112279.6901 - norms/EncoderLSTMBackward_lstmcell1: 112738.5521 - norms/EncoderDense: 347607.7005 - norms/DenseMean: 23870.7718 - norms/DecoderGRU_grucell: 111684.8164 - norms/Dense: 1080.4785 - norms/NeuralDense: 2550.9286 - val_loss: 769.7985 - val_loss/loglike: 769.7985 - val_loss/kldiv: 81.1493
Epoch 29/2000
5/5 [==============================] - 1s 271ms/step - loss: 747.5749 - loss/loglike: 748.5135 - loss/kldiv: 104.8684 - loss/reg: 1029.8818 - weights/log

...

5/5 [==============================] - 1s 252ms/step - loss: 756.3212 - loss/loglike: 692.0684 - loss/kldiv: 56.2182 - loss/reg: 217.7123 - weights/loglike: 1.0000 - weights/kldiv: 1.0000 - weights/reg: 1.0000 - learning_rate: 1.0000e-05 - grads/EncoderLSTMForward_lstmcell2: 2348985.9583 - grads/EncoderLSTMBackward_lstmcell1: 2211337.8750 - grads/EncoderDense: 54312789.3333 - grads/DenseMean: 3623391.9583 - grads/DecoderGRU_grucell: 19434410.5000 - grads/Dense: 4257022.1250 - grads/NeuralDense: 1073249.7708 - norms/EncoderLSTMForward_lstmcell2: 5175038.2917 - norms/EncoderLSTMBackward_lstmcell1: 5137121.4167 - norms/EncoderDense: 28754003.0000 - norms/DenseMean: 1243270.1562 - norms/DecoderGRU_grucell: 2152804.1667 - norms/Dense: 67701.2474 - norms/NeuralDense: 161381.5990 - val_loss: 762.3385 - val_loss/loglike: 710.6254 - val_loss/kldiv: 51.7131
Epoch 1964/2000
5/5 [==============================] - 1s 265ms/step - loss: 756.5902 - loss/loglike: 693.9700 - loss/kldiv: 56.4076 - loss/

5/5 [==============================] - 1s 243ms/step - loss: 759.8126 - loss/loglike: 690.6818 - loss/kldiv: 56.0243 - loss/reg: 217.6974 - weights/loglike: 1.0000 - weights/kldiv: 1.0000 - weights/reg: 1.0000 - learning_rate: 1.0000e-05 - grads/EncoderLSTMForward_lstmcell2: 2361128.0417 - grads/EncoderLSTMBackward_lstmcell1: 2222676.5208 - grads/EncoderDense: 54595765.3333 - grads/DenseMean: 3641593.0833 - grads/DecoderGRU_grucell: 19537144.5000 - grads/Dense: 4276555.2083 - grads/NeuralDense: 1077544.3958 - norms/EncoderLSTMForward_lstmcell2: 5196531.5417 - norms/EncoderLSTMBackward_lstmcell1: 5158428.4167 - norms/EncoderDense: 28873203.0000 - norms/DenseMean: 1248224.4062 - norms/DecoderGRU_grucell: 2160682.5417 - norms/Dense: 68001.2852 - norms/NeuralDense: 162111.4661 - val_loss: 762.3265 - val_loss/loglike: 710.6139 - val_loss/kldiv: 51.7127
Epoch 1973/2000
5/5 [==============================] - 1s 247ms/step - loss: 757.5271 - loss/loglike: 699.5700 - loss/kldiv: 56.6745 - loss/

5/5 [==============================] - 1s 235ms/step - loss: 755.7354 - loss/loglike: 693.0253 - loss/kldiv: 56.2301 - loss/reg: 217.6865 - weights/loglike: 1.0000 - weights/kldiv: 1.0000 - weights/reg: 1.0000 - learning_rate: 1.0000e-05 - grads/EncoderLSTMForward_lstmcell2: 2372776.4792 - grads/EncoderLSTMBackward_lstmcell1: 2233662.2292 - grads/EncoderDense: 54878114.0000 - grads/DenseMean: 3660020.7083 - grads/DecoderGRU_grucell: 19641294.8333 - grads/Dense: 4297635.4167 - grads/NeuralDense: 1082090.5938 - norms/EncoderLSTMForward_lstmcell2: 5218024.7500 - norms/EncoderLSTMBackward_lstmcell1: 5179735.4167 - norms/EncoderDense: 28992403.0000 - norms/DenseMean: 1253178.6562 - norms/DecoderGRU_grucell: 2168560.9167 - norms/Dense: 68301.3223 - norms/NeuralDense: 162841.3346 - val_loss: 762.2964 - val_loss/loglike: 710.5812 - val_loss/kldiv: 51.7152
Epoch 1982/2000
5/5 [==============================] - 1s 244ms/step - loss: 755.1682 - loss/loglike: 695.9670 - loss/kldiv: 56.3633 - loss/

5/5 [==============================] - 1s 193ms/step - loss: 755.1353 - loss/loglike: 698.2856 - loss/kldiv: 56.1538 - loss/reg: 217.6937 - weights/loglike: 1.0000 - weights/kldiv: 1.0000 - weights/reg: 1.0000 - learning_rate: 1.0000e-05 - grads/EncoderLSTMForward_lstmcell2: 2384447.4792 - grads/EncoderLSTMBackward_lstmcell1: 2244594.3750 - grads/EncoderDense: 55154720.3333 - grads/DenseMean: 3677871.1250 - grads/DecoderGRU_grucell: 19744972.5000 - grads/Dense: 4316738.7917 - grads/NeuralDense: 1086210.5417 - norms/EncoderLSTMForward_lstmcell2: 5239518.0000 - norms/EncoderLSTMBackward_lstmcell1: 5201042.4167 - norms/EncoderDense: 29111603.0000 - norms/DenseMean: 1258132.9062 - norms/DecoderGRU_grucell: 2176439.2708 - norms/Dense: 68601.3594 - norms/NeuralDense: 163571.2018 - val_loss: 762.3111 - val_loss/loglike: 710.5921 - val_loss/kldiv: 51.7190
Epoch 1991/2000
5/5 [==============================] - 1s 218ms/step - loss: 754.7156 - loss/loglike: 690.9461 - loss/kldiv: 56.5135 - loss/

5/5 [==============================] - 1s 206ms/step - loss: 758.1549 - loss/loglike: 698.6699 - loss/kldiv: 56.4395 - loss/reg: 217.6792 - weights/loglike: 1.0000 - weights/kldiv: 1.0000 - weights/reg: 1.0000 - learning_rate: 1.0000e-05 - grads/EncoderLSTMForward_lstmcell2: 2394881.6667 - grads/EncoderLSTMBackward_lstmcell1: 2254380.1458 - grads/EncoderDense: 55405729.3333 - grads/DenseMean: 3694163.8333 - grads/DecoderGRU_grucell: 19846723.8333 - grads/Dense: 4338012.0833 - grads/NeuralDense: 1090374.0104 - norms/EncoderLSTMForward_lstmcell2: 5261011.2500 - norms/EncoderLSTMBackward_lstmcell1: 5222335.6667 - norms/EncoderDense: 29230803.0000 - norms/DenseMean: 1263087.1562 - norms/DecoderGRU_grucell: 2184317.6458 - norms/Dense: 68901.3965 - norms/NeuralDense: 164301.0690 - val_loss: 762.3274 - val_loss/loglike: 710.6102 - val_loss/kldiv: 51.7173
Epoch 2000/2000
5/5 [==============================] - 1s 269ms/step - loss: 758.4827 - loss/loglike: 692.4607 - loss/kldiv: 56.1763 - loss/

In [5]:
import latentneural.plot as lnp
import numpy as np
import plotly.express as px
import plotly.graph_objects as go


log_f, _, _, _ = model(neural_data.astype('float'), training=False)
fig_rates = go.Figure(data=go.Heatmap(
    x=list(range(log_f.shape[1])), 
    y=list(range(log_f.shape[-1])), 
    z=np.exp(log_f[1, :, :].numpy().T), colorscale="Blues"))

fig_rates.update_layout(title='Firing Rates of Condition Trial #%d' % (0),
                xaxis_title='Time',
                yaxis_title='Neurons')

fig_rates_n = go.Figure(data=go.Heatmap(
    x=list(range(log_f.shape[1])), 
    y=list(range(log_f.shape[-1])), 
    z=dataset['train_rates'][1, :, :].T, colorscale="Blues"))

fig_rates_n.update_layout(title='Firing Rates of Condition Trial #%d' % (0),
                xaxis_title='Time',
                yaxis_title='Neurons')

fig_rates.show()
fig_rates_n.show()

In [6]:
log_f, (g0, mean, logvar), z, _ = model(neural_data.astype('float'), training=False)

fig_z = go.Figure(data=go.Heatmap(
    x=list(range(log_f.shape[1])), 
    y=list(range(log_f.shape[-1])), 
    z=z.numpy()[0, :, :].T, colorscale="Blues"))

fig_z.update_layout(title='Latent Variables of Condition Trial #%d' % (0),
                xaxis_title='Time',
                yaxis_title='Neurons')

fig_z_n = go.Figure(data=go.Heatmap(
    x=list(range(log_f.shape[1])), 
    y=list(range(log_f.shape[-1])), 
    z=dataset['train_latent'][0, :, :].T, colorscale="Blues"))

fig_z_n.update_layout(title='Latent Variables of Condition Trial #%d' % (0),
                xaxis_title='Time',
                yaxis_title='Neurons')

fig_z.show()
fig_z_n.show()

In [7]:
latent_reconstructed_unsorted = z.numpy().T
latent_original = dataset['train_latent'].T

print(latent_reconstructed_unsorted.shape)
print(latent_original.shape)

(3, 100, 70)
(3, 100, 70)


In [8]:
latent_reconstructed_unsorted_r = latent_reconstructed_unsorted.reshape(
    3, 
    latent_reconstructed_unsorted.shape[1] * latent_reconstructed_unsorted.shape[2]).T

latent_original_r = latent_original.reshape(
    3, 
    latent_original.shape[1] * latent_original.shape[2]).T

In [9]:
from sklearn.linear_model import Ridge

clf = Ridge(alpha=1.0)
clf.fit(latent_reconstructed_unsorted_r, latent_original_r)
print('Score: ', clf.score(latent_reconstructed_unsorted_r, latent_original_r))

predictions = clf.predict(latent_reconstructed_unsorted_r).T.reshape(3, latent_reconstructed_unsorted.shape[1], latent_reconstructed_unsorted.shape[2])

Score:  0.8942098020389541


In [10]:
fig = go.Figure()
condition=0
for d in range(3):
    # Create and style traces
    fig.add_trace(go.Scatter(x=dataset['time_data'], y=latent_original[d,:,condition], name='%d original' % (d),
                            line=dict(color=px.colors.qualitative.Plotly[d], width=10), opacity=0.2))
    fig.add_trace(go.Scatter(x=dataset['time_data'], y=predictions[d,:,condition], name='%d reconstructed' % (d),
                            line = dict(color=px.colors.qualitative.Plotly[d], width=2)))

# Edit the layout
fig.update_layout(title='Latent Trajectories of Condition #%d, Original vs Reconstructed' % (condition),
                xaxis_title='Time',
                yaxis_title='Value')
fig.show()

# Vaidation Performance

In [11]:
log_f, (g0, mean, logvar), z, _ = model(dataset['valid_data'].astype('float'), training=False)
latent_reconstructed_unsorted = z.numpy().T
latent_original = dataset['valid_latent'].T
latent_reconstructed_unsorted_r = latent_reconstructed_unsorted.reshape(
    3, latent_reconstructed_unsorted.shape[1] * latent_reconstructed_unsorted.shape[2]).T
latent_original_r = latent_original.reshape(
    3, latent_original.shape[1] * latent_original.shape[2]).T

clf = Ridge(alpha=1.0)
clf.fit(latent_reconstructed_unsorted_r, latent_original_r)
print('Score: ', clf.score(latent_reconstructed_unsorted_r, latent_original_r))

Score:  0.836141636625236
